# Agent-Based Model on Cat Behavior

### In our project we decided to create 4 total cats with several different traits ranging from hunger levels to personality traits
### Based on the traits each cat has will determine their interactions with each other, objects in the room, and people who walk in the room

In [239]:
from IPython.display import HTML
import numpy as np
import numpy.random as rand
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import random
from PIL import Image
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
import time
%matplotlib inline

To start here is a legend of all potential personality traits and needs our cats may have.

In [241]:
legend= {'Calm' : 'Very relaxed; Gets along with all cats; Gets along with all humans',
         'Shy' : 'Takes a while to warm up, hides away; Does not interact with other cats or humans' ,
         "Playful" : 'Wants to hunt and play; Gets along with Calm cats, Fights with Aggressive cats; Gets along with all humans' ,
         'Aggressive' : 'Will hiss, growl, and bite; Fights with all cats; Fights with humans' 
        } 


#
# Trait	Behavior Around Others
# Shy ≥ 2	Avoids other cats — moves away if another cat is nearby
# Aggressive ≥ 2	Approaches other cats — initiates "conflict" when nearby
# Calm ≥ 2	Doesn't react to other cats (neutral)
# Playful ≥ 2	Moves toward cats (seeks interaction), unless the other cat is aggressive

Because we want our interactions to be as random and organic as possible we will create a class that will help cat decisions!

In [243]:
import random

class Cat:
    def __init__(self, name, personality, image_path):
        self.name = name
        self.image_path = image_path
        self.personality = personality

        self.needs = {'hunger': 0, 'sleep': 0, 'potty': 0}
        self.activity = "roam"

        self.x, self.y = 15, 137  # Start at bed
        self.target = (self.x, self.y)
        self.speed = 1.5

        self.history = []

        # Trackers for new logic
        self.time_roaming = 0
        self.time_playing = 0
        self.last_eaten = -1
        self.last_pottied = -1

    def update_needs(self):
        for need in self.needs:
            self.needs[need] += 1

    def decide_action(self, hour):
        # Sleep at night unless aggressive/playful
        if 22 <= hour or hour < 6:
            if self.personality.get("Aggressive", 0) < 2 and self.personality.get("Playful", 0) < 2:
                self.activity = 'sleeping'
                self.target = (15, 137)
                self.time_roaming = 0
                self.time_playing = 0
                return

        # Force eat if roaming too long without food
        if self.time_roaming >= 3 and self.last_eaten < hour - 3:
            self.do_action("eat")
            return

        # Force sleep after eat + potty + roaming or 2+ plays
        if (self.last_eaten != -1 and self.last_pottied != -1 and
            (self.activity == "roam" or self.time_playing >= 2)):
            self.do_action("sleep")
            self.time_roaming = 0
            self.time_playing = 0
            return

        # Normal priority logic
        priorities = {
            'eat': self.needs['hunger'],
            'sleep': self.needs['sleep'],
            'bathroom': self.needs['potty'],
            'play': self.personality.get('Playful', 0)
        }
        chosen = max(priorities, key=priorities.get)
        self.do_action(chosen)

    def do_action(self, action):
        # Update roaming/playing counters
        if action == "roam":
            self.time_roaming += 1
        else:
            self.time_roaming = 0

        if action == "play":
            self.time_playing += 1
        else:
            self.time_playing = 0

        # Action-specific behaviors
        if action == 'eat':
            self.needs['hunger'] = 0
            self.needs['potty'] += 2
            self.activity = 'eating'
            self.target = (15, 12)
        elif action == 'sleep':
            self.needs['sleep'] = max(0, self.needs['sleep'] - 3)
            self.activity = 'sleeping'
            self.target = (15, 137)
        elif action == 'bathroom':
            self.needs['potty'] = 0
            self.activity = 'bathroom'
            self.target = (140, 137)
        elif action == 'play':
            self.needs['hunger'] += 2
            self.needs['sleep'] += 2
            self.needs['potty'] += 1
            self.activity = 'playing'
            self.target = (140, 12)
        else:
            self.activity = 'roam'
            self.target = self.random_target()

    def move(self):
        dx = self.target[0] - self.x
        dy = self.target[1] - self.y
        dist = (dx**2 + dy**2)**0.5
        if dist > 1:
            self.x += self.speed * dx / dist
            self.y += self.speed * dy / dist
            self.x = min(max(self.x, 0), 150)
            self.y = min(max(self.y, 0), 150)

    def interact_with(self, other_cat):
        if self == other_cat:
            return
        dist = ((self.x - other_cat.x)**2 + (self.y - other_cat.y)**2)**0.5
        if dist < 25:
            if self.personality.get("Shy", 0) >= 2:
                self.activity = "avoiding"
                dx = self.x - other_cat.x
                dy = self.y - other_cat.y
                self.target = (self.x + dx, self.y + dy)
            elif self.personality.get("Aggressive", 0) >= 2:
                self.activity = "confronting"
                self.target = (other_cat.x, other_cat.y)
            elif self.personality.get("Playful", 0) >= 2 and other_cat.personality.get("Aggressive", 0) < 2:
                self.activity = "approaching"
                self.target = (other_cat.x, other_cat.y)

    def log_state(self, hour):
        if self.activity == "eating":
            self.last_eaten = hour
        elif self.activity == "bathroom":
            self.last_pottied = hour

        summary = f"Hour {hour}: {self.name} is {self.activity} at ({int(self.x)}, {int(self.y)})"
        self.history.append({
            'hour': hour,
            'x': self.x,
            'y': self.y,
            'activity': self.activity,
            'needs': self.needs.copy(),
            'summary': summary
        })

    def random_target(self):
        return (random.randint(10, 140), random.randint(10, 140))

    def __repr__(self):
        return f"Cat({self.name}, activity={self.activity})"


In [245]:
cats = [
    Cat('Tito', {
        'Playful': 2,
        'Shy': 1,
        'Calm': 1,
        'Aggressive': 1
    }, "tito.png"),

    Cat('Tobi', {
        'Playful': 1,
        'Shy': 2,
        'Calm': 1,
        'Aggressive': 1
    }, "tobi.png"),

    Cat('Dumpling', {
        'Playful': 1,
        'Shy': 1,
        'Calm': 2,
        'Aggressive': 1
    }, "dumpling.png"),

    Cat('Jiji', {
        'Playful': 1,
        'Shy': 1,
        'Calm': 1,
        'Aggressive': 2
    }, "jiji.png")
]


In [507]:
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import matplotlib.patches as patches
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
import numpy as np
import random
from PIL import Image
from IPython.display import HTML

# Grid size
grid_size = 7
frame_counter = 0
steps_per_hour = 10   # number of frames per hour
total_hours = 12
total_frames = steps_per_hour * total_hours

# Define zones for 7x7 grid
zones = {
    "bed": [(x, y) for x in range(0, 3) for y in range(5, 7)],
    "food": [(x, y) for x in range(0, 3) for y in range(0, 2)],
    "litter": [(x, y) for x in range(4, 7) for y in range(5, 7)]
}

# Cat data
cats = {
    "Tito": {
        "position": [0, 5],
        "image": "tito.png",
        "goal": "bed",
        "personality": {'Playful': 2, 'Shy': 1, 'Calm': 1, 'Aggressive': 1},
        "play_count": 0,
        "fight_count": 0
    },
    "Tobi": {
        "position": [1, 5],
        "image": "tobi.png",
        "goal": "food",
        "personality": {'Playful': 1, 'Shy': 2, 'Calm': 1, 'Aggressive': 1},
        "play_count": 0,
        "fight_count": 0
    },
    "Dumpling": {
        "position": [0, 6],
        "image": "dumpling.png",
        "goal": "litter",
        "personality": {'Playful': 1, 'Shy': 1, 'Calm': 2, 'Aggressive': 1},
        "play_count": 0,
        "fight_count": 0
    },
    "Jiji": {
        "position": [1, 6],
        "image": "jiji.png",
        "goal": "bed",
        "personality": {'Playful': 1, 'Shy': 1, 'Calm': 1, 'Aggressive': 2},
        "play_count": 0,
        "fight_count": 0
    }
}

# Setup plot
fig, ax = plt.subplots(figsize=(6, 6))
ax.set_xlim(0, grid_size)
ax.set_ylim(0, grid_size)
ax.set_xticks(np.arange(0, grid_size+1, 1))
ax.set_yticks(np.arange(0, grid_size+1, 1))
ax.grid(True)
title_text = ax.set_title("Cat Simulation (Hour 1)")

# Draw zones
ax.add_patch(patches.Rectangle((0, 5), 3, 2, edgecolor='blue', facecolor='lightblue'))  # Bed
ax.text(0.1, 6.8, "Bed", fontsize=8, color='blue')

ax.add_patch(patches.Rectangle((4, 5), 3, 2, edgecolor='gray', facecolor='lightgray'))  # Litter
ax.text(4.1, 6.8, "Litter", fontsize=8, color='gray')

ax.add_patch(patches.Rectangle((0, 0), 3, 2, edgecolor='green', facecolor='lightgreen'))  # Food
ax.text(0.1, 0.2, "Food", fontsize=8, color='green')

# Load and draw cats
cat_artists = {}
play_markers = []
fight_markers = []

def load_cat_image(path, zoom=0.15):
    image = Image.open(path)
    return OffsetImage(image, zoom=zoom)

for name, info in cats.items():
    img = load_cat_image(info["image"])
    ab = AnnotationBbox(img, (info["position"][0] + 0.5, info["position"][1] + 0.5), frameon=False)
    cat_artists[name] = ab
    ax.add_artist(ab)

def are_adjacent(pos1, pos2):
    return abs(pos1[0] - pos2[0]) + abs(pos1[1] - pos2[1]) == 1

def can_play(cat1, cat2):
    if cat1["personality"].get("Aggressive", 0) >= 2 or cat2["personality"].get("Aggressive", 0) >= 2:
        return False
    if cat1["personality"].get("Playful", 0) >= 2 and cat2["personality"].get("Playful", 0) >= 2:
        return True
    if cat1["personality"].get("Playful", 0) >= 2 and cat2["personality"].get("Calm", 0) >= 2:
        return True
    if cat2["personality"].get("Playful", 0) >= 2 and cat1["personality"].get("Calm", 0) >= 2:
        return True
    return False

def will_fight(cat1, cat2):
    a1 = cat1["personality"].get("Aggressive", 0)
    a2 = cat2["personality"].get("Aggressive", 0)
    p1 = cat1["personality"].get("Playful", 0)
    p2 = cat2["personality"].get("Playful", 0)
    return (a1 >= 2 or a2 >= 2) or (p1 >= 2 and a2 >= 2) or (p2 >= 2 and a1 >= 2)

def show_play_marker(pos1, pos2):
    x = (pos1[0] + pos2[0]) / 2 + 0.5
    y = (pos1[1] + pos2[1]) / 2 + 0.5
    marker = ax.plot(x, y, 'ro', markersize=6)[0]
    play_markers.append(marker)

def show_fight_marker(pos1, pos2):
    x = (pos1[0] + pos2[0]) / 2 + 0.5
    y = (pos1[1] + pos2[1]) / 2 + 0.5
    marker = ax.text(x, y, 'X', color='red', fontsize=14, weight='bold', ha='center', va='center')
    fight_markers.append(marker)

def get_neighbors(pos, exclude_name):
    return [info["position"] for name, info in cats.items()
            if name != exclude_name and are_adjacent(pos, info["position"])]

def move_cat(name, position):
    info = cats[name]
    x, y = position
    goal_zone = zones[info["goal"]]
    shy = info["personality"].get("Shy", 0) >= 2

    neighbors = get_neighbors(position, name)
    if shy and neighbors:
        dx = x - neighbors[0][0]
        dy = y - neighbors[0][1]
        if dx != 0 and 0 <= x + np.sign(dx) < grid_size:
            return [x + np.sign(dx), y]
        if dy != 0 and 0 <= y + np.sign(dy) < grid_size:
            return [x, y + np.sign(dy)]

    closest = min(goal_zone, key=lambda g: abs(g[0] - x) + abs(g[1] - y))
    dx = closest[0] - x
    dy = closest[1] - y

    if abs(dx) > abs(dy):
        new_x = x + np.sign(dx)
        if 0 <= new_x < grid_size:
            return [new_x, y]
    elif dy != 0:
        new_y = y + np.sign(dy)
        if 0 <= new_y < grid_size:
            return [x, new_y]

    return random.choice([
        [x + 1, y] if x + 1 < grid_size else [x, y],
        [x - 1, y] if x - 1 >= 0 else [x, y],
        [x, y + 1] if y + 1 < grid_size else [x, y],
        [x, y - 1] if y - 1 >= 0 else [x, y]
    ])

def update(frame):
    global frame_counter
    frame_counter += 1

    current_hour = frame // steps_per_hour + 1
    if current_hour <= total_hours:
        title_text.set_text(f"Cat Simulation (Hour {current_hour})")

    for marker in play_markers:
        marker.remove()
    play_markers.clear()
    for marker in fight_markers:
        marker.remove()
    fight_markers.clear()

    for name, info in cats.items():
        if frame_counter < 10:
            continue
        info["position"] = move_cat(name, info["position"])
        cat_artists[name].xybox = (info["position"][0] + 0.5, info["position"][1] + 0.5)

    interacted = set()
    for name1, info1 in cats.items():
        for name2, info2 in cats.items():
            if name1 == name2:
                continue
            pair = tuple(sorted((name1, name2)))
            if pair in interacted:
                continue
            if are_adjacent(info1["position"], info2["position"]):
                if can_play(info1, info2):
                    show_play_marker(info1["position"], info2["position"])
                    cats[name1]["play_count"] += 1
                    cats[name2]["play_count"] += 1
                elif will_fight(info1, info2):
                    show_fight_marker(info1["position"], info2["position"])
                    cats[name1]["fight_count"] += 1
                    cats[name2]["fight_count"] += 1
                interacted.add(pair)

    return list(cat_artists.values()) + play_markers + fight_markers

def print_final_stats():
    print("\n🎉 Final Interaction Counts:")
    for name, info in cats.items():
        print(f"{name}: Plays = {info['play_count']}, Fights = {info['fight_count']}")

anim = animation.FuncAnimation(fig, update, frames=total_frames, interval=500, blit=True)
plt.show()
HTML(anim.to_jshtml())

<IPython.core.display.Javascript object>

Here you can find out who our cats are and what their personality traits are!

The start of the simulation for the visualization.

In [509]:
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import matplotlib.patches as patches
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
import numpy as np
import random
from PIL import Image
from IPython.display import HTML

# Grid size
grid_size = 7
frame_counter = 0
steps_per_hour = 10   # number of frames per hour
total_hours = 12
total_frames = steps_per_hour * total_hours

# Define zones for 7x7 grid
zones = {
    "bed": [(x, y) for x in range(0, 3) for y in range(5, 7)],
    "food": [(x, y) for x in range(0, 3) for y in range(0, 2)],
    "litter": [(x, y) for x in range(4, 7) for y in range(5, 7)]
}

# Cat data
cats = {
    "Tito": {
        "position": [0, 5],
        "image": "tito.png",
        "goal": "bed",
        "personality": {'Playful': 2, 'Shy': 1, 'Calm': 1, 'Aggressive': 1},
        "play_count": 0,
        "fight_count": 0,
        "interaction_count": 0,  # Track total interactions
        "last_interaction_hour": 0,  # Track when the cat last interacted
        "original_goal": "bed",  # Keep track of original goal
        "fed": False  # Track if the cat has eaten recently
    },
    "Tobi": {
        "position": [1, 5],
        "image": "tobi.png",
        "goal": "food",
        "personality": {'Playful': 1, 'Shy': 2, 'Calm': 1, 'Aggressive': 1},
        "play_count": 0,
        "fight_count": 0,
        "interaction_count": 0,
        "last_interaction_hour": 0,
        "original_goal": "food",
        "fed": False
    },
    "Dumpling": {
        "position": [0, 6],
        "image": "dumpling.png",
        "goal": "litter",
        "personality": {'Playful': 1, 'Shy': 1, 'Calm': 2, 'Aggressive': 1},
        "play_count": 0,
        "fight_count": 0,
        "interaction_count": 0,
        "last_interaction_hour": 0,
        "original_goal": "litter",
        "fed": False
    },
    "Jiji": {
        "position": [1, 6],
        "image": "jiji.png",
        "goal": "bed",
        "personality": {'Playful': 1, 'Shy': 1, 'Calm': 1, 'Aggressive': 2},
        "play_count": 0,
        "fight_count": 0,
        "interaction_count": 0,
        "last_interaction_hour": 0,
        "original_goal": "bed",
        "fed": False
    }
}

# Setup plot
fig, ax = plt.subplots(figsize=(6, 6))
ax.set_xlim(0, grid_size)
ax.set_ylim(0, grid_size)
ax.set_xticks(np.arange(0, grid_size+1, 1))
ax.set_yticks(np.arange(0, grid_size+1, 1))
ax.grid(True)
title_text = ax.set_title("Cat Simulation (Hour 1)")

# Draw zones
ax.add_patch(patches.Rectangle((0, 5), 3, 2, edgecolor='blue', facecolor='lightblue'))  # Bed
ax.text(0.1, 6.8, "Bed", fontsize=8, color='blue')

ax.add_patch(patches.Rectangle((4, 5), 3, 2, edgecolor='gray', facecolor='lightgray'))  # Litter
ax.text(4.1, 6.8, "Litter", fontsize=8, color='gray')

ax.add_patch(patches.Rectangle((0, 0), 3, 2, edgecolor='green', facecolor='lightgreen'))  # Food
ax.text(0.1, 0.2, "Food", fontsize=8, color='green')

# Load and draw cats
cat_artists = {}
play_markers = []
fight_markers = []
goal_change_texts = []  # To display goal change notifications

def load_cat_image(path, zoom=0.15):
    image = Image.open(path)
    return OffsetImage(image, zoom=zoom)

for name, info in cats.items():
    img = load_cat_image(info["image"])
    ab = AnnotationBbox(img, (info["position"][0] + 0.5, info["position"][1] + 0.5), frameon=False)
    cat_artists[name] = ab
    ax.add_artist(ab)

def are_adjacent(pos1, pos2):
    return abs(pos1[0] - pos2[0]) + abs(pos1[1] - pos2[1]) == 1

def can_play(cat1, cat2):
    if cat1["personality"].get("Aggressive", 0) >= 2 or cat2["personality"].get("Aggressive", 0) >= 2:
        return False
    if cat1["personality"].get("Playful", 0) >= 2 and cat2["personality"].get("Playful", 0) >= 2:
        return True
    if cat1["personality"].get("Playful", 0) >= 2 and cat2["personality"].get("Calm", 0) >= 2:
        return True
    if cat2["personality"].get("Playful", 0) >= 2 and cat1["personality"].get("Calm", 0) >= 2:
        return True
    return False

def will_fight(cat1, cat2):
    a1 = cat1["personality"].get("Aggressive", 0)
    a2 = cat2["personality"].get("Aggressive", 0)
    p1 = cat1["personality"].get("Playful", 0)
    p2 = cat2["personality"].get("Playful", 0)
    return (a1 >= 2 or a2 >= 2) or (p1 >= 2 and a2 >= 2) or (p2 >= 2 and a1 >= 2)

def show_play_marker(pos1, pos2):
    x = (pos1[0] + pos2[0]) / 2 + 0.5
    y = (pos1[1] + pos2[1]) / 2 + 0.5
    marker = ax.plot(x, y, 'ro', markersize=6)[0]
    play_markers.append(marker)

def show_fight_marker(pos1, pos2):
    x = (pos1[0] + pos2[0]) / 2 + 0.5
    y = (pos1[1] + pos2[1]) / 2 + 0.5
    marker = ax.text(x, y, 'X', color='red', fontsize=14, weight='bold', ha='center', va='center')
    fight_markers.append(marker)

def show_goal_change_text(name, pos, new_goal, reason):
    x, y = pos[0] + 0.5, pos[1] + 0.5
    text = ax.text(x, y + 0.7, f"{name}: → {new_goal}", color='purple', fontsize=8, 
                  ha='center', va='center', bbox=dict(facecolor='white', alpha=0.7))
    goal_change_texts.append((text, frame_counter + 20))  # Display for 20 frames

def get_neighbors(pos, exclude_name):
    return [info["position"] for name, info in cats.items()
            if name != exclude_name and are_adjacent(pos, info["position"])]

def move_cat(name, info, current_hour):
    x, y = info["position"]
    
    # Check if cat is in its target zone
    is_in_food_zone = tuple(info["position"]) in zones["food"]
    
    # Reset interactions and change goal after eating
    if info["goal"] == "food" and is_in_food_zone and not info["fed"]:
        # Reset interaction counts
        info["interaction_count"] = 0
        info["last_interaction_hour"] = current_hour
        info["fed"] = True
        
        # Return to original goal
        if info["original_goal"] != "food":
            info["goal"] = info["original_goal"]
            show_goal_change_text(name, info["position"], info["goal"], "reset")
    
    # Check if the cat needs to change goal to food after 3 interactions
    elif info["interaction_count"] >= 3 and info["goal"] != "food":
        info["goal"] = "food"
        info["fed"] = False  # Need to eat again
        show_goal_change_text(name, info["position"], "food", "3+ interactions")
    
    # Check if cat hasn't interacted for 3+ hours
    elif current_hour >= 4:  # After sleeping hours
        hours_without_interaction = current_hour - info["last_interaction_hour"]
        if hours_without_interaction >= 3 and info["goal"] != "food" and info["last_interaction_hour"] > 0:
            info["goal"] = "food"
            info["fed"] = False  # Need to eat again
            show_goal_change_text(name, info["position"], "food", "no interaction")
    
    goal_zone = zones[info["goal"]]
    shy = info["personality"].get("Shy", 0) >= 2

    neighbors = get_neighbors(info["position"], name)
    if shy and neighbors:
        dx = x - neighbors[0][0]
        dy = y - neighbors[0][1]
        if dx != 0 and 0 <= x + np.sign(dx) < grid_size:
            return [x + np.sign(dx), y]
        if dy != 0 and 0 <= y + np.sign(dy) < grid_size:
            return [x, y + np.sign(dy)]

    closest = min(goal_zone, key=lambda g: abs(g[0] - x) + abs(g[1] - y))
    dx = closest[0] - x
    dy = closest[1] - y

    if abs(dx) > abs(dy):
        new_x = x + np.sign(dx)
        if 0 <= new_x < grid_size:
            return [new_x, y]
    elif dy != 0:
        new_y = y + np.sign(dy)
        if 0 <= new_y < grid_size:
            return [x, new_y]

    return random.choice([
        [x + 1, y] if x + 1 < grid_size else [x, y],
        [x - 1, y] if x - 1 >= 0 else [x, y],
        [x, y + 1] if y + 1 < grid_size else [x, y],
        [x, y - 1] if y - 1 >= 0 else [x, y]
    ])

def update(frame):
    global frame_counter
    frame_counter += 1

    current_hour = frame // steps_per_hour + 1
    if current_hour <= total_hours:
        title_text.set_text(f"Cat Simulation (Hour {current_hour})")

    # Remove expired goal change texts
    for i in range(len(goal_change_texts) - 1, -1, -1):
        text, expiry_frame = goal_change_texts[i]
        if frame_counter >= expiry_frame:
            text.remove()
            goal_change_texts.pop(i)

    # Cats sleep during hours 1 and 2
    if current_hour in [1, 2]:
        return list(cat_artists.values()) + [text for text, _ in goal_change_texts]

    for marker in play_markers:
        marker.remove()
    play_markers.clear()
    for marker in fight_markers:
        marker.remove()
    fight_markers.clear()

    # Track which cats interacted this frame
    interacted_cats = set()

    for name, info in cats.items():
        # Only move after initial frames
        if frame_counter >= 10:
            info["position"] = move_cat(name, info, current_hour)
            cat_artists[name].xybox = (info["position"][0] + 0.5, info["position"][1] + 0.5)

    interacted_pairs = set()
    for name1, info1 in cats.items():
        for name2, info2 in cats.items():
            if name1 == name2:
                continue
            pair = tuple(sorted((name1, name2)))
            if pair in interacted_pairs:
                continue
            if are_adjacent(info1["position"], info2["position"]):
                interaction_occurred = False
                
                if can_play(info1, info2):
                    show_play_marker(info1["position"], info2["position"])
                    cats[name1]["play_count"] += 1
                    cats[name2]["play_count"] += 1
                    interaction_occurred = True
                elif will_fight(info1, info2):
                    show_fight_marker(info1["position"], info2["position"])
                    cats[name1]["fight_count"] += 1
                    cats[name2]["fight_count"] += 1
                    interaction_occurred = True
                    
                if interaction_occurred:
                    cats[name1]["interaction_count"] += 1
                    cats[name2]["interaction_count"] += 1
                    cats[name1]["last_interaction_hour"] = current_hour
                    cats[name2]["last_interaction_hour"] = current_hour
                    interacted_cats.add(name1)
                    interacted_cats.add(name2)
                    
                interacted_pairs.add(pair)

    return list(cat_artists.values()) + play_markers + fight_markers + [text for text, _ in goal_change_texts]

def print_final_stats():
    print("\n🎉 Final Interaction Counts:")
    for name, info in cats.items():
        print(f"{name}: Plays = {info['play_count']}, Fights = {info['fight_count']}, Total = {info['interaction_count']}")

anim = animation.FuncAnimation(fig, update, frames=total_frames, interval=500, blit=True)
plt.show()
HTML(anim.to_jshtml())

<IPython.core.display.Javascript object>

In [505]:
print_final_stats()


🎉 Final Interaction Counts:
Tito: Plays = 1, Fights = 84, Total = 1
Tobi: Plays = 0, Fights = 10, Total = 10
Dumpling: Plays = 1, Fights = 2, Total = 0
Jiji: Plays = 0, Fights = 96, Total = 0
